In [1]:
import pandas as pd
#  Importing libraries and module and some setting for notebook

import pandas as pd
import re
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np
from scipy.sparse import csr_matrix
import sparse_dot_topn.sparse_dot_topn as ct  #Cosine Similarity
import time
from tqdm import tqdm

In [2]:
def wikinorm(univ_string):
    from googlesearch import search
    from nltk.metrics import edit_distance
    from operator import itemgetter
    from numpy.random import default_rng
    rng = default_rng()
    results = search(univ_string, lang="en", num_results=3,advanced=True, sleep_interval=rng.uniform(1, 5))
    univ_name = univ_string.split(",")[0]
    u_results = [i.title for i in results if "Category:" not in i.title]
    return sorted([tuple((j,edit_distance(univ_name, j))) for j in u_results],key=itemgetter(1))[0][0]


In [3]:
def replace_uppercase_words(text):
    words = text.split()
    all_uppercase = all(word.isupper() for word in words)
    all_lowercase = all(word.islower() for word in words)
    if all_uppercase or all_lowercase:
        return text
    else:
        result = []
        for word in words:
            w = word.strip()
            if not w.isupper() and not w.islower():
                result.append(w)
        return " ".join(result).strip()

In [4]:
outdir="wos_processed_data"
univ = pd.read_excel(f"{outdir}/wos_institution_locations.xlsx")

from pandarallel import pandarallel
pandarallel.initialize(progress_bar=True, nb_workers=4)

univ["Institution_harm"] = univ["Institution"].parallel_apply(replace_uppercase_words)
print(len(univ))

INFO: Pandarallel will run on 4 workers.
INFO: Pandarallel will use standard multiprocessing data transfer (pipe) to transfer data between the main process and workers.

https://nalepae.github.io/pandarallel/troubleshooting/


178638


In [5]:
univ.sample(100)

UT (Unique WOS ID)                        Institution   
153271  WOS:000784587900008                          Univ Pisa  \
159800  WOS:000810042500002        China Japan Friendship Hosp   
130931  WOS:000691922800007            Karl Franzens Univ Graz   
1500    WOS:000292944600012                                CNR   
113964  WOS:000618210000032               Karolinska Univ Hosp   
...                     ...                                ...   
160284  WOS:000812227000009        Univ Appl Sci Upper Austria   
29314   WOS:000381396400013                   Univ Southampton   
17045   WOS:000347046200017                Charles Univ Prague   
164118  WOS:000832954200001  Nanjing Univ Aeronaut & Astronaut   
109992  WOS:000604257500070             KTH Royal Inst Technol   

               Country                   Institution_harm  
153271           Italy                          Univ Pisa  
159800           China        China Japan Friendship Hosp  
130931         Austria            Karl Franzens Univ Graz  
1500             Italy                                CNR  
113964          Sweden               Karolinska Univ Hosp  
...                ...                                ...  
160284         Austria        Univ Appl Sci Upper Austria  
29314   United Kingdom                   Univ Southampton  
17045   Czech Republic                Charles Univ Prague  
164118           China  Nanjing Univ Aeronaut & Astronaut  
109992          Sweden                 Royal Inst Technol  

[100 rows x 4 columns]

In [6]:
univ_norm = univ.groupby("Country", as_index=False)["Institution_harm"].value_counts()
# univ_norm["search_for"] = univ_norm["Institution"]+", " + univ_norm["Country"]+ ", wikipedia"
univ_norm.sample(100)

Country                          Institution_harm  count
8168          Croatia        Inst Adriat Crops & Karst Reclamat      1
3417            China                         Ctr Eye & Vis Res      1
1034            China                   Westlake Inst Adv Study     13
13427           Italy                             Macerata Hosp      1
8071            China  Key Lab Ecoind Green Technol Fujian Prov      1
...               ...                                       ...    ...
17230  United Kingdom                             Univ Kingston      6
8847           France                               Univ Artois      8
16071           Spain          Catalonia Geriatr & Gerontol Soc      1
6357            China              Wuxi Huace Elect Syst Co Ltd      1
9049           France                      Excelia Business Sch      3

[100 rows x 3 columns]

In [7]:
# from pandarallel import pandarallel
# pandarallel.initialize(progress_bar=True, nb_workers=2)
#
# df_sample["search_result"] = df_sample["search_for"].parallel_apply(wikinorm)

In [8]:
def ngrams(string, n=3):

    string = re.sub(r'[,-./]|\sBD',r'', string)
    ngrams = zip(*[string[i:] for i in range(n)])
    return [''.join(ngram) for ngram in ngrams]

# calculate the similarity between two vectors of TF-IDF values the Cosine Similarity is usually used.
# result matrix in a very sparse terms and Scikit-learn deals with this nicely by returning a sparse CSR matrix.

def awesome_cossim_top(A, B, ntop, lower_bound=0):
    # force A and B as a CSR matrix.
    # If they have already been CSR, there is no overhead
    A = A.tocsr()
    B = B.tocsr()
    M, _ = A.shape
    _, N = B.shape

    idx_dtype = np.int32

    nnz_max = M*ntop

    indptr = np.zeros(M+1, dtype=idx_dtype)
    indices = np.zeros(nnz_max, dtype=idx_dtype)
    data = np.zeros(nnz_max, dtype=A.dtype)

    ct.sparse_dot_topn(
        M, N, np.asarray(A.indptr, dtype=idx_dtype),
        np.asarray(A.indices, dtype=idx_dtype),
        A.data,
        np.asarray(B.indptr, dtype=idx_dtype),
        np.asarray(B.indices, dtype=idx_dtype),
        B.data,
        ntop,
        lower_bound,
        indptr, indices, data)

    return csr_matrix((data,indices,indptr),shape=(M,N))

# unpacks the resulting sparse matrix

def get_matches_df(sparse_matrix, name_vector, top=None):
    non_zeros = sparse_matrix.nonzero()

    sparserows = non_zeros[0]
    sparsecols = non_zeros[1]

    if top:
        nr_matches = top
    else:
        nr_matches = sparsecols.size

    left_side = np.empty([nr_matches], dtype=object)
    right_side = np.empty([nr_matches], dtype=object)
    similarity = np.zeros(nr_matches)

    for index in range(0, nr_matches):
        left_side[index] = name_vector[sparserows[index]]
        right_side[index] = name_vector[sparsecols[index]]
        similarity[index] = sparse_matrix.data[index]

    return pd.DataFrame({'left_side': left_side,
                          'right_side': right_side,
                           'similarity': similarity})


def discrepancy_filter(df):
    f_df = df.copy()
    tokenlist = ["Med", "Hosp", "Tech", "Univ", "Acad", "Poly"]
    for token in tokenlist:
        f_df = f_df[~(((f_df["right_side"].str.contains(token))&
                       (~f_df["left_side"].str.contains(token)))
                      |
                ((f_df["left_side"].str.contains(token))&
                 (~f_df["right_side"].str.contains(token))))].copy()
    return f_df


# Define a function to get the high and low counts for each row
def get_high_low_counts(row):
    if row['left_count'] > row['right_count']:
        high_count = row['left_count']
        low_count = row['right_count']
    else: #row['left_count'] < row['right_count']:
        high_count = row['right_count']
        low_count = row['left_count']
    # else:
    #     if len(row['left_side']) > len(row['right_side']):
    #             high_count = len(row['left_side'])
    #             low_count = len(row['right_side'])
    #     else:
    #             high_count = len(row['right_side'])
    #             low_count = len(row['left_side'])
    return pd.Series([high_count, low_count])

In [9]:
merger = pd.DataFrame()

# for i in tqdm(filter(lambda c: c!="China", list(univ_norm["Country"].unique()))):
for i in tqdm(list(univ_norm["Country"].unique())):
    sub_inst = univ_norm[univ_norm["Country"]==i].reset_index()
    types = sub_inst['Institution_harm']
    vectorizer = TfidfVectorizer(min_df=1, analyzer=ngrams)
    tf_idf_matrix = vectorizer.fit_transform(types)
    t1 = time.time()
    matches = awesome_cossim_top(tf_idf_matrix, tf_idf_matrix.transpose(), 10, 0.8 if i!="China" else 0.9)
    t = time.time()-t1

    # store the  matches into new dataframe called matched_df and printing 10 samples
    matches_df = get_matches_df(matches, types)
    matches_df = matches_df[matches_df['similarity'] < 0.99999] # For removing all exact matches
    matches_df = discrepancy_filter(matches_df).reset_index(drop=True)
    matches_df["Country"] = i
    # matches_df = matches_df[pd.DataFrame(np.sort(matches_df[['left_side','right_side']].values,1)).duplicated()]
    # matches_df = matches_df[~matches_df[['left_side', 'right_side']].apply(frozenset, axis=1).duplicated()]
    merger = pd.concat([merger,matches_df], ignore_index=True)

for s in ["left","right"]:
    merger[f"{s}_count"] = merger[f"{s}_side"].apply(lambda x: len(univ[univ["Institution_harm"] == x]))

# Apply the function to create a new column
merger[['high_count', 'low_count']] = merger.apply(get_high_low_counts, axis=1)

# Use apply again to create the high_side and low_side columns
merger['high_side'] = merger.apply(lambda row: row['left_side'] if row['left_count'] > row['right_count'] else row['right_side'], axis=1)
merger['low_side'] = merger.apply(lambda row: row['left_side'] if row['left_count'] <= row['right_count'] else row['right_side'], axis=1)

# Drop the high_count and low_count columns if they are not needed
# merger.drop(['high_count', 'low_count'], axis=1, inplace=True)

100%|██████████| 31/31 [00:00<00:00, 31.97it/s]


In [10]:
fuzzymerger = merger[["Country","low_side","high_side","high_count","low_count","similarity"]].drop_duplicates()
fuzzymerger = fuzzymerger.sort_values(by=["low_side","high_count"], ascending=[True,False])
fuzzymerger = fuzzymerger.drop_duplicates(subset=["Country","low_side"]).sort_values(by="high_count", ascending=True).reset_index(drop=True)
print(len(fuzzymerger))
univ_harm = univ.copy()
univ_harm["merge_iter"] = 0
for i,row in tqdm(fuzzymerger.iterrows()):
    univ_harm.loc[((univ_harm["Country"]==row["Country"])&
                   (univ_harm["Institution_harm"]==row["low_side"])),"merge_iter"] += 1
    univ_harm.loc[((univ_harm["Country"]==row["Country"])&
                   (univ_harm["Institution_harm"]==row["low_side"])),"Institution_harm"] = row["high_side"]

1916


1916it [01:11, 26.94it/s]


In [11]:
# fuzzymerger[fuzzymerger["Country"]=="China"]

In [12]:
# univ_harm[((univ_harm["merge_iter"]>0) & (univ_harm["Country"]=="Italy"))]

In [13]:
univ_harm.loc[((univ_harm["merge_iter"]>0) & (univ_harm["Country"]=="Italy")&
           (univ_harm["Institution"].str.lower().str.contains("sapien"))&
            (univ_harm["Institution"].str.lower().str.contains("univ"))), "Institution_harm"] = "Sapienza Univ Rome"

In [14]:
univ_harm[["Institution","Institution_harm"]].nunique()

Institution         19821
Institution_harm    16646
dtype: int64

In [16]:
univ_harm.sample(500)

UT (Unique WOS ID)                   Institution         Country   
49282   WOS:000428099700011                Univ Sheffield  United Kingdom  \
51975   WOS:000432981300002              Chinese Acad Sci           China   
64618   WOS:000459693000011             Babes Bolyai Univ         Romania   
163145  WOS:000828102100001                   Xidian Univ           China   
99690   WOS:000566510600001           Fora Forest Technol           Spain   
...                     ...                           ...             ...   
1567    WOS:000293492500004                    Univ Essex  United Kingdom   
73076   WOS:000476471800022                 Shanghai Univ           China   
137096  WOS:000715426400001               Queen Mary Hosp           China   
164978  WOS:000836819000003  Manchester Metropolitan Univ  United Kingdom   
32973   WOS:000390181300013       Univ Complutense Madrid           Spain   

                    Institution_harm  merge_iter  
49282                 Univ Sheffield           0  
51975               Chinese Acad Sci           0  
64618              Babes Bolyai Univ           0  
163145                   Xidian Univ           0  
99690            Fora Forest Technol           0  
...                              ...         ...  
1567                      Univ Essex           0  
73076                  Shanghai Univ           0  
137096               Queen Mary Hosp           0  
164978  Manchester Metropolitan Univ           0  
32973        Univ Complutense Madrid           0  

[500 rows x 5 columns]

In [15]:
univ_harm.to_excel(f"{outdir}/wos_institution_locations_harmonized.xlsx", index=False)